## import necessary packages 

In [1]:
from datetime import datetime
from shapely.geometry import Point
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
import folium
from folium.plugins import MarkerCluster
from folium.plugins import FastMarkerCluster

## read in CSVs 

In [2]:
calls_derecho = pd.read_csv('./data/911_Phone_Calls_Derecho_050320_050420.csv')
calls_tornado = pd.read_csv('./data/911_Phone_Calls_Tornado_030320.csv')
dispatch_derecho = pd.read_csv('./data/Computer_Aided_Dispatch_Data_Derecho_Incidents_050320-050420.csv', skiprows = 3)
dispatch_tornado = pd.read_csv('./data/Computer_Aided_Dispatch_Data_Tornado_Incidents_030320.csv', skiprows = 3)
zipcodes = gpd.read_file('./data/zipcodes.geojson')
#dispatch = pd.read_csv('./data/Metro_Nashville_Police_Department_Calls_for_Service.csv')
dispatch = pd.read_csv('./data/dispatch.csv')

## clean up metro dispatch data

dispatch[["call_date", "call_time"]]= dispatch.pop("Call Received").str.split(" ", n = 1, expand = True)

In [5]:
dispatch['Geometry'] = dispatch.apply(lambda x: Point((float(x.Longitude), 
                                                         float(x.Latitude))), 
                                        axis=1)

In [3]:
dispatch.shape

(7426, 21)

In [6]:
dispatch_geo = gpd.GeoDataFrame(dispatch, 
                           crs = zipcodes.crs, 
                           geometry = dispatch['Geometry'])
type(dispatch_geo)                                         

geopandas.geodataframe.GeoDataFrame

In [35]:
dispatch_zip = gpd.sjoin(dispatch_geo, zipcodes, op = 'within')
dispatch_zip = dispatch_zip.drop(columns = ['index_right'])
dispatch_zip.head(2)

Unnamed: 0    Event Number  Complaint Number  Shift  Tencode  \
9             9  PD202000176531      2.020015e+10    NaN       43   
209         209  PD202000356687               NaN    NaN       96   

     Tencode Description Tencode Suffix Tencode Suffix Description  \
9                    NaN             PM                        NaN   
209                  NaN            NaN                        NaN   

    Disposition Code  Disposition Description  ...  RPA Latitude Longitude  \
9                 11                      NaN  ...  0.0   36.129   -86.725   
209               12                      NaN  ...  0.0   36.089   -86.609   

            Mapped Location   call_date    call_time  \
9    POINT (-86.725 36.129)  03/03/2020  02:18:22 PM   
209  POINT (-86.609 36.089)  05/03/2020  07:46:51 AM   

                              Geometry                    geometry    zip  \
9    POINT (-86.72499999999999 36.129)  POINT (-86.72500 36.12900)  37217   
209  POINT (-86.60899999999999 36.089)  POINT (-86.60900 36.08900)  37217   

       po_name  
9    NASHVILLE  
209  NASHVILLE  

[2 rows x 25 columns]

In [ ]:
dispatch.shape

In [40]:
dispatch.isnull().sum()

Unnamed: 0                       0
Event Number                     0
Complaint Number              7025
Shift                         7426
Tencode                          0
Tencode Description           7426
Tencode Suffix                1344
Tencode Suffix Description    1973
Disposition Code                 0
Disposition Description       7426
Block                         5973
Street Name                   5773
Unit Dispatched                814
Sector                        1302
Zone                           666
RPA                           1204
Latitude                      6560
Longitude                     6560
Mapped Location               6560
call_date                        0
call_time                        0
Geometry                         0
geometry                         0
dtype: int64

dispatch_march_tornado=dispatch[dispatch["call_date"].isin(["03/03/2020"])]
dispatch_march_tornado

dispatch_may_storm=dispatch[dispatch["call_date"].isin(["05/03/2020", "05/04/2020"])]
dispatch_may_storm

## Rename columns 

In [8]:
calls_derecho = calls_derecho.rename(columns = {'Seizure DateTime': 'DateTime', 'CallTypeId': 'Call Type', 'ALI Latitude': 'Latitude', 'ALI Longitude': 'Longitude', 'Cell Tower Address': 'Cell Tower'})

In [9]:
calls_tornado = calls_tornado.rename(columns = {'Seizure DateTime': 'DateTime', 'CallTypeId': 'Call Type', 'ALI Latitude': 'Latitude', 'ALI Longitude': 'Longitude', 'Cell Tower Address': 'Cell Tower'})

In [10]:
dispatch_derecho = dispatch_derecho.rename(columns = {'IncidentDate': 'DateTime', 'Latitude1': 'Latitude', 'Longitude1': 'Longitude', 'IncidentTypeDescription1': 'Incident Description'})

In [11]:
dispatch_tornado = dispatch_tornado.rename(columns = {'IncidentDate': 'DateTime', 'Latitude1': 'Latitude', 'Longitude1': 'Longitude', 'IncidentTypeDescription1': 'Incident Description'})

## Add geometry points to data sets 

In [12]:
calls_derecho['Geometry'] = calls_derecho.apply(lambda x: Point((float(x.Longitude), 
                                                         float(x.Latitude))), 
                                        axis=1)

In [13]:
calls_tornado['Geometry'] = calls_tornado.apply(lambda x: Point((float(x.Longitude), 
                                                         float(x.Latitude))), 
                                        axis=1)

In [14]:
dispatch_derecho['Geometry'] = dispatch_derecho.apply(lambda x: Point((float(x.Longitude), 
                                                         float(x.Latitude))), 
                                        axis=1)

In [15]:
dispatch_tornado['Geometry'] = dispatch_tornado.apply(lambda x: Point((float(x.Longitude), 
                                                         float(x.Latitude))), 
                                        axis=1)

## check data

In [37]:
calls_derecho.head()

DateTime  Call Type   Latitude  Longitude             Cell Tower  \
0  5/3/2020 16:30  911 Calls  36.247802 -86.716847        WIRELESS CALLER   
1  5/3/2020 16:30  911 Calls  36.143108 -86.800621    1161 21ST AV S - SE   
2  5/3/2020 16:30  911 Calls  36.100516 -87.056329  8013 C MCCRORY LN - N   
3  5/3/2020 16:30  911 Calls  36.130021 -86.927819     5758 RIVER RD - SW   
4  5/3/2020 16:31  911 Calls  36.142380 -86.881882   3744B ANNEX AVE - SE   

                                       Geometry                    geometry  
0                  POINT (-86.716847 36.247802)  POINT (-86.71685 36.24780)  
1  POINT (-86.80062099999999 36.14310800000001)  POINT (-86.80062 36.14311)  
2          POINT (-87.05632900000001 36.100516)  POINT (-87.05633 36.10052)  
3                  POINT (-86.927819 36.130021)  POINT (-86.92782 36.13002)  
4           POINT (-86.88188199999999 36.14238)  POINT (-86.88188 36.14238)

In [ ]:
calls_tornado.head()

In [38]:
dispatch_derecho.head()

DateTime            Location   Latitude  Longitude  \
0  5/3/2020 4:31:07 PM    901 KENWICK CT W  36.046877 -86.962526   
1  5/3/2020 4:32:18 PM       8036 ARBOR DR  36.082491 -86.940680   
2  5/3/2020 4:32:23 PM   119 DUE WEST AV E  36.248029 -86.716875   
3  5/3/2020 4:33:04 PM  630 GALLATIN PKE S  36.256491 -86.714817   
4  5/3/2020 4:33:52 PM   615 W HILLWOOD DR  36.129690 -86.879834   

  Incident Description                          Geometry  \
0    ELECTRICAL HAZARD  POINT (-86.96252641 36.04687715)   
1    ELECTRICAL HAZARD  POINT (-86.94067952 36.08249081)   
2       NOT ALERT COPD  POINT (-86.71687484 36.24802948)   
3       ABDOMINAL PAIN  POINT (-86.71481656 36.25649117)   
4    ELECTRICAL HAZARD  POINT (-86.87983392 36.12968971)   

                     geometry  
0  POINT (-86.96253 36.04688)  
1  POINT (-86.94068 36.08249)  
2  POINT (-86.71687 36.24803)  
3  POINT (-86.71482 36.25649)  
4  POINT (-86.87983 36.12969)

In [ ]:
dispatch_tornado.head()

In [ ]:
zipcodes.head()

## shape check

In [ ]:
calls_derecho.shape

In [ ]:
calls_tornado.shape

In [ ]:
dispatch_derecho.shape

In [ ]:
dispatch_tornado.shape

## count Cell Towers and Incident Descriptions

In [ ]:
calls_derecho['Cell Tower'].value_counts()

In [ ]:
calls_tornado['Cell Tower'].value_counts()

In [ ]:
dispatch_derecho['Incident Description'].value_counts()

In [ ]:
dispatch_tornado['Incident Description'].value_counts()

## count null values

In [ ]:
calls_derecho.isnull().sum()

In [ ]:
calls_tornado.isnull().sum()

In [ ]:
dispatch_derecho.isnull().sum()

In [ ]:
dispatch_tornado.isnull().sum()

map1 = sns.FacetGrid(dispactch_derecho, col = 'Incident Description')
map1.map(sns.barplot, "DateTime")

plt.hist(dispatch_derecho['Incident Description'], bins = 10);

## clean zipcodes data and create geodata frames for all datasets

In [16]:
zipcodes = zipcodes[['zip', 'po_name', 'geometry']]

In [17]:
derecho_calls_geo = gpd.GeoDataFrame(calls_derecho, 
                           crs = zipcodes.crs, 
                           geometry = calls_derecho['Geometry'])
type(derecho_calls_geo)

geopandas.geodataframe.GeoDataFrame

In [18]:
tornado_calls_geo = gpd.GeoDataFrame(calls_tornado, 
                           crs = zipcodes.crs, 
                           geometry = calls_tornado['Geometry'])
type(tornado_calls_geo)

geopandas.geodataframe.GeoDataFrame

In [19]:
dispatch_derecho_geo = gpd.GeoDataFrame(dispatch_derecho, 
                           crs = zipcodes.crs, 
                           geometry = dispatch_derecho['Geometry'])
type(dispatch_derecho_geo)

geopandas.geodataframe.GeoDataFrame

In [20]:
dispatch_tornado_geo = gpd.GeoDataFrame(dispatch_tornado, 
                           crs = zipcodes.crs, 
                           geometry = dispatch_tornado['Geometry'])
type(dispatch_tornado_geo)

geopandas.geodataframe.GeoDataFrame

## merge data sets with zipcodes

In [30]:
derecho_calls_zip = gpd.sjoin(derecho_calls_geo, zipcodes, op = 'within')
derecho_calls_zip = derecho_calls_zip.drop(columns = ['index_right'])
derecho_calls_zip

DateTime  Call Type   Latitude  Longitude  \
0     5/3/2020 16:30  911 Calls  36.247802 -86.716847   
68    5/3/2020 16:44  911 Calls  36.265547 -86.736116   
78    5/3/2020 16:46  911 Calls  36.250710 -86.689766   
79    5/3/2020 16:46  911 Calls  36.259485 -86.678717   
100   5/3/2020 16:51  911 Calls  36.253467 -86.730366   
...              ...        ...        ...        ...   
829   5/3/2020 19:11  911 Calls  36.165276 -86.780491   
880   5/3/2020 19:20  911 Calls  36.168324 -86.783089   
892   5/3/2020 19:22  911 Calls  36.165715 -86.782079   
1504  5/3/2020 23:25  911 Calls  36.004472 -86.695497   
1507  5/3/2020 23:29  911 Calls  36.174341 -86.783195   

                               Cell Tower  \
0                         WIRELESS CALLER   
68              524 BOYDS HILLTOP DR - SW   
78            607E LARKIN SPRINGS RD - SW   
79            96 D VANDIVER DR - SECTOR S   
100       619 DUE WEST AVE. W - NE SECTOR   
...                                   ...   
829                          315 4TH AV N   
880              500 5TH AV - SECTOR SW N   
892            315-B 4TH AV - SECTOR NW N   
1504        1598-A RAGSDALE RD - SECTOR N   
1507  404 JAMES ROBERTSON PKWY - N SECTOR   

                                          Geometry  \
0                     POINT (-86.716847 36.247802)   
68            POINT (-86.73611600000001 36.265547)   
78             POINT (-86.68976600000001 36.25071)   
79            POINT (-86.67871700000001 36.259485)   
100                   POINT (-86.730366 36.253467)   
...                                            ...   
829                   POINT (-86.780491 36.165276)   
880                   POINT (-86.783089 36.168324)   
892   POINT (-86.78207900000001 36.16571500000001)   
1504                  POINT (-86.695497 36.004472)   
1507          POINT (-86.78319499999999 36.174341)   

                        geometry    zip    po_name  
0     POINT (-86.71685 36.24780)  37115    MADISON  
68    POINT (-86.73612 36.26555)  37115    MADISON  
78    POINT (-86.68977 36.25071)  37115    MADISON  
79    POINT (-86.67872 36.25948)  37115    MADISON  
100   POINT (-86.73037 36.25347)  37115    MADISON  
...                          ...    ...        ...  
829   POINT (-86.78049 36.16528)  37219  NASHVILLE  
880   POINT (-86.78309 36.16832)  37219  NASHVILLE  
892   POINT (-86.78208 36.16572)  37219  NASHVILLE  
1504  POINT (-86.69550 36.00447)  37027  BRENTWOOD  
1507  POINT (-86.78319 36.17434)  37201  NASHVILLE  

[1425 rows x 9 columns]

In [31]:
tornado_calls_zip = gpd.sjoin(tornado_calls_geo, zipcodes, op = 'within')
tornado_calls_zip = tornado_calls_zip.drop(columns = ['index_right'])
tornado_calls_zip

DateTime  Call Type   Latitude  Longitude  \
0    3/3/2020 0:34  911 Calls  36.072708 -86.665779   
10   3/3/2020 0:38  911 Calls  36.052055 -86.648331   
64   3/3/2020 0:53  911 Calls  36.050048 -86.650629   
194  3/3/2020 1:29  911 Calls  36.068298 -86.681550   
234  3/3/2020 1:40  911 Calls  36.058578 -86.699745   
..             ...        ...        ...        ...   
444  3/3/2020 4:25  911 Calls  36.190487 -86.833237   
209  3/3/2020 1:34  911 Calls  36.308312 -86.720581   
323  3/3/2020 2:10  911 Calls  36.311104 -86.707214   
328  3/3/2020 2:12  911 Calls  36.311102 -86.707213   
232  3/3/2020 1:39  911 Calls  36.189438 -86.799713   

                               Cell Tower  \
0              620 Richards RD - N Sector   
10              745 BELL RD - OMNI Sector   
64                    5646 AMALIE DR - SE   
194         3930 APACHE TRAIL - SE SECTOR   
234                  5067 COLEMONT DR - N   
..                                    ...   
444          2111 Summitt Ave - Sector SW   
209      1000 S CARTWRIGHT ST - SECTOR SW   
323              456 MOSS TRL - SE Sector   
328                       WIRELESS CALLER   
232  2025B METRO CENTER BLVD. - SW SECTOR   

                                 Geometry                    geometry    zip  \
0            POINT (-86.665779 36.072708)  POINT (-86.66578 36.07271)  37013   
10           POINT (-86.648331 36.052055)  POINT (-86.64833 36.05205)  37013   
64   POINT (-86.65062900000001 36.050048)  POINT (-86.65063 36.05005)  37013   
194           POINT (-86.68155 36.068298)  POINT (-86.68155 36.06830)  37013   
234  POINT (-86.69974499999999 36.058578)  POINT (-86.69974 36.05858)  37013   
..                                    ...                         ...    ...   
444          POINT (-86.833237 36.190487)  POINT (-86.83324 36.19049)  37218   
209  POINT (-86.72058100000001 36.308312)  POINT (-86.72058 36.30831)  37072   
323  POINT (-86.70721400000001 36.311104)  POINT (-86.70721 36.31110)  37072   
328  POINT (-86.707213 36.31110200000001)  POINT (-86.70721 36.31110)  37072   
232          POINT (-86.799713 36.189438)  POINT (-86.79971 36.18944)  37228   

            po_name  
0           ANTIOCH  
10          ANTIOCH  
64          ANTIOCH  
194         ANTIOCH  
234         ANTIOCH  
..              ...  
444       NASHVILLE  
209  GOODLETTSVILLE  
323  GOODLETTSVILLE  
328  GOODLETTSVILLE  
232       NASHVILLE  

[434 rows x 9 columns]

In [32]:
dispatch_derecho_zip = gpd.sjoin(dispatch_derecho_geo, zipcodes, op = 'within')
dispatch_derecho_zip = dispatch_derecho_zip.drop(columns = ['index_right'])
dispatch_derecho_zip

DateTime                       Location   Latitude  \
0     5/3/2020 4:31:07 PM               901 KENWICK CT W  36.046877   
1     5/3/2020 4:32:18 PM                  8036 ARBOR DR  36.082491   
17    5/3/2020 4:39:57 PM           8715 OLD HARDING PKE  36.012524   
88    5/3/2020 5:12:40 PM                   7205 MARK DR  36.065849   
116   5/3/2020 5:25:03 PM             1651 CHICKERING RD  36.059848   
..                    ...                            ...        ...   
409   5/3/2020 8:00:32 PM               3531 HUNTLAND DR  36.274720   
460   5/3/2020 8:40:46 PM        1211 MEDICAL CENTER DR   36.142407   
604  5/3/2020 11:30:49 PM  2ND AV N / JUNIOR GILLIAM WAY  36.174401   
606  5/3/2020 11:39:35 PM         2022 ROSA L PARKS BLVD  36.188362   
610  5/3/2020 11:42:08 PM         2022 ROSA L PARKS BLVD  36.188362   

     Longitude                         Incident Description  \
0   -86.962526                            ELECTRICAL HAZARD   
1   -86.940680                            ELECTRICAL HAZARD   
17  -87.024584                            ELECTRICAL HAZARD   
88  -86.928772                            ELECTRICAL HAZARD   
116 -86.874532                         ENTRAPMENT / TRAPPED   
..         ...                                          ...   
409 -86.842008          DIFFICULTY SPEAKING BETWEEN BREATHS   
460 -86.801598  GENERAL ALARM COMMERCIAL   INDUSTRIAL BUILD   
604 -86.783024           CHEST PAIN - CLAMMY OR COLD SWEATS   
606 -86.798090   TRAUMATIC INJURIES NOT DANGEROUS BODY AREA   
610 -86.798090            REQUEST ADDITIONAL FIRE RESOURCES   

                                   Geometry                    geometry  \
0          POINT (-86.96252641 36.04687715)  POINT (-86.96253 36.04688)   
1          POINT (-86.94067952 36.08249081)  POINT (-86.94068 36.08249)   
17   POINT (-87.02458403999999 36.01252365)  POINT (-87.02458 36.01252)   
88         POINT (-86.92877244 36.06584867)  POINT (-86.92877 36.06585)   
116  POINT (-86.87453247000001 36.05984766)  POINT (-86.87453 36.05985)   
..                                      ...                         ...   
409  POINT (-86.84200841000001 36.27471998)  POINT (-86.84201 36.27472)   
460        POINT (-86.80159753 36.14240652)  POINT (-86.80160 36.14241)   
604        POINT (-86.78302399 36.17440126)  POINT (-86.78302 36.17440)   
606        POINT (-86.79808982 36.18836237)  POINT (-86.79809 36.18836)   
610        POINT (-86.79808982 36.18836237)  POINT (-86.79809 36.18836)   

       zip       po_name  
0    37221     NASHVILLE  
1    37221     NASHVILLE  
17   37221     NASHVILLE  
88   37221     NASHVILLE  
116  37221     NASHVILLE  
..     ...           ...  
409  37189  WHITES CREEK  
460  37232     NASHVILLE  
604  37201     NASHVILLE  
606  37228     NASHVILLE  
610  37228     NASHVILLE  

[625 rows x 9 columns]

In [33]:
dispatch_tornado_zip = gpd.sjoin(dispatch_tornado_geo, zipcodes, op = 'within')
dispatch_tornado_zip = dispatch_tornado_zip.drop(columns = ['index_right'])
dispatch_tornado_zip

DateTime                     Location   Latitude  Longitude  \
0    3/3/2020 12:36:34 AM      6205 COCKRILL BEND CIR   36.182002 -86.894052   
1    3/3/2020 12:37:24 AM     7337 COCKRILL BEND BLVD   36.175666 -86.894978   
2    3/3/2020 12:38:17 AM         110 TUNE AIRPORT DR   36.179299 -86.883727   
17   3/3/2020 12:44:49 AM      7337 COCKRILL BEND BLVD  36.175666 -86.894978   
19   3/3/2020 12:45:10 AM           7135 CENTENNIAL PL  36.176893 -86.879949   
..                    ...                          ...        ...        ...   
231   3/3/2020 4:06:14 AM             200 E WEBSTER ST  36.251077 -86.716657   
234   3/3/2020 4:16:53 AM         368 BRITISH WOODS DR  36.092959 -86.654322   
236   3/3/2020 4:21:34 AM                 115 LAURA AV  36.234591 -86.630412   
240   3/3/2020 4:27:57 AM              200 ATHENS WAY   36.195772 -86.799250   
259   3/3/2020 4:57:48 AM  I24 W / HICKORY HOLLOW PKWY  36.039720 -86.649099   

                                  Incident Description  \
0          GENERAL ALARM COMMERCIAL   INDUSTRIAL BUILD   
1          GENERAL ALARM COMMERCIAL   INDUSTRIAL BUILD   
2               STRUCTURE FIRE COMMERCIAL   INDUSTRIAL   
17                    BUILDING ENTRAPMENT  UNCONFIRMED   
19                                    INSIDE FUEL ODOR   
..                                                 ...   
231                        CITIZEN ASSIST  NON MEDICAL   
234                DIFFICULTY SPEAKING BETWEEN BREATHS   
236  DIFFICULTY SPEAKING BETWEEN BREATHS OTHER LUNG...   
240  SMOKE DETECTOR ALARM COMMERCIAL   INDUSTRIAL B...   
259                                    UNKNOWN STATUS:   

                                   Geometry                    geometry  \
0          POINT (-86.89405212 36.18200191)  POINT (-86.89405 36.18200)   
1      POINT (-86.89497756999999 36.175666)  POINT (-86.89498 36.17567)   
2           POINT (-86.8837274 36.17929946)  POINT (-86.88373 36.17930)   
17     POINT (-86.89497756999999 36.175666)  POINT (-86.89498 36.17567)   
19   POINT (-86.87994904999999 36.17689288)  POINT (-86.87995 36.17689)   
..                                      ...                         ...   
231        POINT (-86.71665675 36.25107722)  POINT (-86.71666 36.25108)   
234         POINT (-86.65432195 36.0929593)  POINT (-86.65432 36.09296)   
236  POINT (-86.63041192999999 36.23459081)  POINT (-86.63041 36.23459)   
240        POINT (-86.79925022 36.19577205)  POINT (-86.79925 36.19577)   
259        POINT (-86.64909858 36.03971988)  POINT (-86.64910 36.03972)   

       zip      po_name  
0    37209    NASHVILLE  
1    37209    NASHVILLE  
2    37209    NASHVILLE  
17   37209    NASHVILLE  
19   37209    NASHVILLE  
..     ...          ...  
231  37115      MADISON  
234  37217    NASHVILLE  
236  37138  OLD HICKORY  
240  37228    NASHVILLE  
259  37013      ANTIOCH  

[260 rows x 9 columns]

## merge dispatch_zip geo to the above

derecho_dispatch_zip = gpd.sjoin(derecho_calls_zip, dispatch_zip, op = 'within')
derecho_dispatch_zip

## nashville map 

In [41]:
nashville = (36.16784, -86.77816)

nash_map = folium.Map(location = nashville, zoom_start = 10)

In [42]:
poly_zip=zipcodes[zipcodes['zip'].isin(['37207', '37072', '37189', '37218','37015','37080'])]
poly_zip.shape

(11, 3)

In [43]:
tcalls_in_nw = tornado_calls_zip[tornado_calls_zip['zip'].isin(['37207', '37072', '37189', '37218','37015','37080'])]
tcalls_in_nw.shape

(43, 9)

In [46]:
dcalls_in_nw = derecho_calls_zip[derecho_calls_zip['zip'].isin(['37207', '37072', '37189', '37218','37015','37080'])]
dcalls_in_nw.shape

(78, 9)

In [47]:
dderecho_in_nw = dispatch_derecho_zip[dispatch_derecho_zip['zip'].isin(['37207', '37072', '37189', '37218','37015','37080'])]
dderecho_in_nw.shape

(35, 9)

In [48]:
dtornado_in_nw = dispatch_tornado_zip[dispatch_tornado_zip['zip'].isin(['37207', '37072', '37189', '37218','37015','37080'])]
dtornado_in_nw.shape

(13, 9)

In [56]:
cluster_map = MarkerCluster().add_to(nash_map)

folium.GeoJson(poly_zip).add_to(nash_map)
marker_cluster = MarkerCluster().add_to(nash_map)
for row_index, row_values in tcalls_in_nw.iterrows():
    loc = [row_values['Latitude'], row_values['Longitude']]
    pop = str(row_values['Cell Tower'])
    icon=folium.Icon(color="red",icon="phone", prefix='fa')
    
for row_index, row_values in dcalls_in_nw.iterrows():
    loc = [row_values['Latitude'], row_values['Longitude']]
    pop = str(row_values['Cell Tower'])
    icon=folium.Icon(color="darkblue",icon="phone", prefix='fa')

for row_index, row_values in dderecho_in_nw.iterrows():
    loc = [row_values['Latitude'], row_values['Longitude']]
    pop = str(row_values['Location'])
    icon=folium.Icon(color="orange",icon="ambulance", prefix='fa')

for row_index, row_values in dtornado_in_nw.iterrows():
    loc = [row_values['Latitude'], row_values['Longitude']]
    pop = str(row_values['Location'])
    icon=folium.Icon(color="darkpurple",icon="ambulance", prefix='fa')
    marker = folium.Marker(
        location = loc, 
        popup = pop,
    icon = icon) 
    
    marker.add_to(cluster_map)

    
#cluster_map_nw.save('../maps/clusternw.html')

#cluster_map_nw


In [57]:
nash_map

In [ ]:
#poly = zipcodes.loc[zipcodes['zip'] == '37207']
#polygon37207.shape